In [1]:
import polars as pl
import numpy as np
import pandas as pd
import math
from polars import col

# 1. Exploratory Data Analysis (EDA)


## 1.1 Data Inspection


In [122]:
df_raw = pl.read_csv("Amazon Sale Report.csv")

## First 5 rows of the dataset


In [123]:
print(df_raw.head())

shape: (5, 24)
┌───────┬─────────────┬──────────┬─────────────┬───┬─────────────┬───────┬────────────┬────────────┐
│ index ┆ Order-ID    ┆ Date     ┆ Status      ┆ … ┆ promotion-i ┆ B2B   ┆ fulfilled- ┆ Unnamed:22 │
│ ---   ┆ ---         ┆ ---      ┆ ---         ┆   ┆ ds          ┆ ---   ┆ by         ┆ ---        │
│ i64   ┆ str         ┆ str      ┆ str         ┆   ┆ ---         ┆ bool  ┆ ---        ┆ str        │
│       ┆             ┆          ┆             ┆   ┆ str         ┆       ┆ str        ┆            │
╞═══════╪═════════════╪══════════╪═════════════╪═══╪═════════════╪═══════╪════════════╪════════════╡
│ 0     ┆ 405-8078784 ┆ 04-30-22 ┆ Cancelled   ┆ … ┆ null        ┆ false ┆ Easy Ship  ┆ null       │
│       ┆ -5731545    ┆          ┆             ┆   ┆             ┆       ┆            ┆            │
│ 1     ┆ 171-9198151 ┆ 04-30-22 ┆ Shipped -   ┆ … ┆ Amazon PLCC ┆ false ┆ Easy Ship  ┆ null       │
│       ┆ -1101146    ┆          ┆ Delivered   ┆   ┆ Free-Financ ┆       ┆  

## Data Types


In [124]:
df_raw.glimpse(max_items_per_column=5)

Rows: 128977
Columns: 24
$ index               <i64> 0, 1, 2, 3, 4
$ Order-ID            <str> '405-8078784-5731545', '171-9198151-1101146', '404-0687676-7273146', '403-9615377-8133951', '407-1069790-7240320'
$ Date                <str> '04-30-22', '04-30-22', '04-30-22', '04-30-22', '04-30-22'
$ Status              <str> 'Cancelled', 'Shipped - Delivered to Buyer', 'Shipped', 'Cancelled', 'Shipped'
$ Fulfilment          <str> 'Merchant', 'Merchant', 'Amazon', 'Merchant', 'Amazon'
$ Sales-Channel       <str> 'Amazon.in', 'Amazon.in', 'Amazon.in', 'Amazon.in', 'Amazon.in'
$ ship-service-level  <str> 'Standard', 'Standard', 'Expedited', 'Standard', 'Expedited'
$ Style               <str> 'SET389', 'JNE3781', 'JNE3371', 'J0341', 'JNE3671'
$ SKU                 <str> 'SET389-KR-NP-S', 'JNE3781-KR-XXXL', 'JNE3371-KR-XL', 'J0341-DR-L', 'JNE3671-TU-XXXL'
$ Category            <str> 'Set', 'kurta', 'kurta', 'Western Dress', 'Top'
$ Size                <str> 'S', '3XL', 'XL', 'L', '3XL'
$ ASIN 

### Max Bits Needed to Store Numeric Columns


In [125]:
def max_bits_and_suit_type(number, type_):
    max_bits = math.ceil(math.log2(number))

    if type_.is_float() and max_bits <= 32:
        type_ = pl.Float32
    if type_.is_integer():
        if max_bits <= 8:
            type_ = pl.Int8()
        elif max_bits <= 16:
            type_ = pl.Int16
        elif max_bits <= 32:
            type_ = pl.Int32
        else:
            type_ = pl.Int64

    return max_bits, type_

In [126]:
for col_ in df_raw:
    if col_.dtype.is_numeric():
        max_bits, suit_type = max_bits_and_suit_type(col_.max(), col_.dtype)
        print(
            f'{col_.name:>18}({str(col_.dtype):>7}): {max_bits:>2} bits, suit type: {suit_type}'
        )

             index(  Int64): 17 bits, suit type: Int32
               Qty(  Int64):  4 bits, suit type: Int8
            Amount(Float64): 13 bits, suit type: Float32
  ship-postal-code(Float64): 20 bits, suit type: Float32


In [127]:
df_raw['Unnamed:22'].unique()

shape: (2,)
Series: 'Unnamed:22' [str]
[
	null
	"False"
]

### Potential Issues

- Date Column is not of type date.
- Index Column is not Useful.
- Qty Column Need to be converted to int8 to reduce memory.
- Amount Column Need to be converted to Float32 to reduce memory.
- ship-postal-code Column Need to be converted to Int32 to reduce memory.
- Unnamed:22 Must be bool not to be string


## 1.2 Summary Statistics


In [128]:
num_cols = [col.name for col in df_raw if col.dtype.is_numeric()]
str_cols = [col.name for col in df_raw if col.dtype == pl.String]

### Numerical Columns Statistics


In [129]:
df_raw.select(num_cols).describe()

shape: (9, 5)
┌────────────┬──────────────┬──────────┬────────────┬──────────────────┐
│ statistic  ┆ index        ┆ Qty      ┆ Amount     ┆ ship-postal-code │
│ ---        ┆ ---          ┆ ---      ┆ ---        ┆ ---              │
│ str        ┆ f64          ┆ f64      ┆ f64        ┆ f64              │
╞════════════╪══════════════╪══════════╪════════════╪══════════════════╡
│ count      ┆ 128975.0     ┆ 128975.0 ┆ 121180.0   ┆ 128940.0         │
│ null_count ┆ 2.0          ┆ 2.0      ┆ 7797.0     ┆ 37.0             │
│ mean       ┆ 64487.0      ┆ 0.904431 ┆ 648.561465 ┆ 463969.927594    │
│ std        ┆ 37232.019822 ┆ 0.313354 ┆ 281.211687 ┆ 191475.956294    │
│ min        ┆ 0.0          ┆ 0.0      ┆ 0.0        ┆ 110001.0         │
│ 25%        ┆ 32244.0      ┆ 1.0      ┆ 449.0      ┆ 382421.0         │
│ 50%        ┆ 64487.0      ┆ 1.0      ┆ 605.0      ┆ 500033.0         │
│ 75%        ┆ 96731.0      ┆ 1.0      ┆ 788.0      ┆ 600024.0         │
│ max        ┆ 128974.0     ┆ 15.0     ┆ 5584.0     ┆ 989898.0         │
└────────────┴──────────────┴──────────┴────────────┴──────────────────┘

### Categorical Columns Statistics


In [130]:
df_raw.select(str_cols).to_pandas().describe()

Order-ID      Date   Status Fulfilment Sales-Channel  \
count                128977    128977   128977     128977        128977   
unique               120379        92       14          4             3   
top     171-5057375-2831560  05-03-22  Shipped     Amazon     Amazon.in   
freq                     12      2085    77804      89698        128851   

       ship-service-level    Style           SKU Category    Size        ASIN  \
count              128977   128977        128975   128975  128975      128975   
unique                  3     1378          7195        9      11        7190   
top             Expedited  JNE3797  JNE3797-KR-L      Set       M  B09SDXFFQ1   
freq                88615     4224           773    50284   22711         773   

       Courier-Status currency  ship-city   ship-state ship-country  \
count          122103   121180     128942       128940       128940   
unique              3        1       8955           69            1   
top           Shipped      INR  BENGALURU  MAHARASHTRA           IN   
freq           109487   121180      11217        22260       128940   

                                       promotion-ids fulfilled-by Unnamed:22  
count                                          79820        39275      79923  
unique                                          5787            1          1  
top     IN Core Free Shipping 2015/04/08 23-48-5-108    Easy Ship      False  
freq                                           46100        39275      79923

#### Simple Patterns


In [131]:
df_raw.group_by('Qty')\
    .agg(col("Amount").mean())\
    .filter(
    col("Qty").is_not_null() &
        col("Amount").is_not_nan()
).plot.bar(x='Qty', y='Amount', title='Mean Amount by Quantity')

:Bars   [Qty]   (Amount)

we can infer that the mean amount is increasing with the quantity.


# 2: Data Preprocessing


## 2.1 Handling Missing Values


In [132]:
df_raw = df_raw.drop('index')

In [133]:
print("Null Portion of the data:")
for i in ((df_raw.null_count()/df_raw.height*100)):
    if i[0] > 0:
        print(
            f"{i.name:>18} : {i[0]:>8.5f} %,\
 null-count: {df_raw[i.name].null_count():>5},\
 mode: {df_raw[i.name].mode()[0]}")

Null Portion of the data:
               SKU :  0.00155 %, null-count:     2, mode: JNE3797-KR-L
          Category :  0.00155 %, null-count:     2, mode: Set
              Size :  0.00155 %, null-count:     2, mode: M
              ASIN :  0.00155 %, null-count:     2, mode: B09SDXFFQ1
    Courier-Status :  5.32963 %, null-count:  6874, mode: Shipped
               Qty :  0.00155 %, null-count:     2, mode: 1
          currency :  6.04526 %, null-count:  7797, mode: INR
            Amount :  6.04526 %, null-count:  7797, mode: None
         ship-city :  0.02714 %, null-count:    35, mode: BENGALURU
        ship-state :  0.02869 %, null-count:    37, mode: MAHARASHTRA
  ship-postal-code :  0.02869 %, null-count:    37, mode: 201301.0
      ship-country :  0.02869 %, null-count:    37, mode: IN
     promotion-ids : 38.11300 %, null-count: 49157, mode: None
               B2B :  0.00310 %, null-count:     4, mode: False
      fulfilled-by : 69.54883 %, null-count: 89702, mode: None
     

In [134]:
col_null_remove = ['SKU', 'ASIN', 'ship-city',
                   'ship-state', 'ship-postal-code', 'ship-country']


col_null_mode_imputation = ['Category', 'Size', 'Qty', 'B2B']

# amount with 0
# currency with "Missed"
# drop fulfilled-by, Unnamed:22 columns
# Courier-Status later in the notebook

In [135]:
df_cleaned = df_raw.drop(['fulfilled-by', 'Unnamed:22'])

df_cleaned = df_cleaned.drop_nulls(
    subset=col_null_remove
)
for col_ in col_null_mode_imputation:
    df_cleaned = df_cleaned.with_columns(
        col(col_).fill_null(df_cleaned[col_].mode())
    )

df_cleaned = df_cleaned.with_columns(
    col("Amount").fill_null(0),
    col("currency").fill_null("Missed"),
)

df_cleaned.null_count()

shape: (1, 21)
┌──────────┬──────┬────────┬────────────┬───┬─────────────────┬──────────────┬───────────────┬─────┐
│ Order-ID ┆ Date ┆ Status ┆ Fulfilment ┆ … ┆ ship-postal-cod ┆ ship-country ┆ promotion-ids ┆ B2B │
│ ---      ┆ ---  ┆ ---    ┆ ---        ┆   ┆ e               ┆ ---          ┆ ---           ┆ --- │
│ u32      ┆ u32  ┆ u32    ┆ u32        ┆   ┆ ---             ┆ u32          ┆ u32           ┆ u32 │
│          ┆      ┆        ┆            ┆   ┆ u32             ┆              ┆               ┆     │
╞══════════╪══════╪════════╪════════════╪═══╪═════════════════╪══════════════╪═══════════════╪═════╡
│ 0        ┆ 0    ┆ 0      ┆ 0          ┆ … ┆ 0               ┆ 0            ┆ 49145         ┆ 0   │
└──────────┴──────┴────────┴────────────┴───┴─────────────────┴──────────────┴───────────────┴─────┘

### Let's check Courier-Status column


In [136]:
df_cleaned['Courier-Status'].unique()

shape: (4,)
Series: 'Courier-Status' [str]
[
	"Cancelled"
	null
	"Unshipped"
	"Shipped"
]

### while Courier-Status is null what the most Status is?


In [137]:
df_cleaned.group_by(['Courier-Status', 'Status']).agg(
    col('Status').count().name.suffix('_count'),
).filter(
    col('Courier-Status').is_null()
).sort(by='Status_count', descending=True)

shape: (3, 3)
┌────────────────┬──────────────────────────────┬──────────────┐
│ Courier-Status ┆ Status                       ┆ Status_count │
│ ---            ┆ ---                          ┆ ---          │
│ str            ┆ str                          ┆ u32          │
╞════════════════╪══════════════════════════════╪══════════════╡
│ null           ┆ Cancelled                    ┆ 6858         │
│ null           ┆ Shipped - Delivered to Buyer ┆ 8            │
│ null           ┆ Shipped - Returned to Seller ┆ 3            │
└────────────────┴──────────────────────────────┴──────────────┘

the most relationship strong When `Status` is **Cancelled** <br>
but i want to replace any null value in `Courier-Status` with <br>
its value when `Status` the most in when `Courier-Status` is not null <br>
Lets See How!


In [138]:
df_cleaned.group_by(['Courier-Status', 'Status']).agg(
    col('Status').count().name.suffix('_count'),
).filter(
    col('Courier-Status').is_not_null() &
    col('Status').is_in(
        ['Cancelled', 'Shipped - Delivered to Buyer',

         'Shipped - Returned to Seller', 'IN']
    )
).sort(by='Status_count', descending=True).to_pandas()

Courier-Status                        Status  Status_count
0        Shipped  Shipped - Delivered to Buyer         28752
1      Cancelled                     Cancelled          5838
2      Unshipped                     Cancelled          5629
3        Shipped  Shipped - Returned to Seller          1947

As you can infer we will replace null with

1. "Shipped" when `Status` is "Shipped - Delivered to Buyer" or "Shipped - Returned to Seller"
2. "Cancelled" when `Status` is "Cancelled" (the most in when `Courier-Status` is not null)


In [139]:
df_cleaned = df_cleaned.with_columns(
    pl.when(col("Courier-Status").is_null()
            & (col("Status") == 'Cancelled'))
    .then(col("Courier-Status").fill_null("Cancelled"))

    .when(col("Courier-Status").is_null() &
          (col("Status").is_in(["Shipped - Delivered to Buyer", "Shipped - Returned to Seller"])))
    .then(col("Courier-Status").fill_null("Shipped"))

    .otherwise(col("Courier-Status"))
)
df_cleaned.null_count()

shape: (1, 21)
┌──────────┬──────┬────────┬────────────┬───┬─────────────────┬──────────────┬───────────────┬─────┐
│ Order-ID ┆ Date ┆ Status ┆ Fulfilment ┆ … ┆ ship-postal-cod ┆ ship-country ┆ promotion-ids ┆ B2B │
│ ---      ┆ ---  ┆ ---    ┆ ---        ┆   ┆ e               ┆ ---          ┆ ---           ┆ --- │
│ u32      ┆ u32  ┆ u32    ┆ u32        ┆   ┆ ---             ┆ u32          ┆ u32           ┆ u32 │
│          ┆      ┆        ┆            ┆   ┆ u32             ┆              ┆               ┆     │
╞══════════╪══════╪════════╪════════════╪═══╪═════════════════╪══════════════╪═══════════════╪═════╡
│ 0        ┆ 0    ┆ 0      ┆ 0          ┆ … ┆ 0               ┆ 0            ┆ 49145         ┆ 0   │
└──────────┴──────┴────────┴────────────┴───┴─────────────────┴──────────────┴───────────────┴─────┘

In [140]:
promotion_types = [
    'Amazon PLCC Free-Financing Universal Merchant',
    'IN Core Free Shipping'
]

In [141]:
temp_df = df_cleaned.filter(
    col('promotion-ids').is_not_null()
).select('promotion-ids')

for i in range(10):
    index = np.random.randint(temp_df.height)
    print(index, temp_df[index].item().split(','))

30493 ['IN Core Free Shipping 2015/04/08 23-48-5-108']
78164 ['IN Core Free Shipping 2015/04/08 23-48-5-108']
16031 ['IN Core Free Shipping 2015/04/08 23-48-5-108']
5055 ['Amazon PLCC Free-Financing Universal Merchant AAT-WNKTBO3K27EJC', 'Amazon PLCC Free-Financing Universal Merchant AAT-QX3UCCJESKPA2', 'Amazon PLCC Free-Financing Universal Merchant AAT-5QQ7BIYYQEDN2', 'Amazon PLCC Free-Financing Universal Merchant AAT-DSJ2QRXXWXVMQ', 'Amazon PLCC Free-Financing Universal Merchant AAT-CXJHMC2YJUK76', 'Amazon PLCC Free-Financing Universal Merchant AAT-CC4FAVTYR4X7C', 'Amazon PLCC Free-Financing Universal Merchant AAT-XXRCW6NZEPZI4', 'Amazon PLCC Free-Financing Universal Merchant AAT-R7GXNZWISTRFA', 'Amazon PLCC Free-Financing Universal Merchant AAT-EOKPWFWYW7Y6I', 'Amazon PLCC Free-Financing Universal Merchant AAT-ZYL5UPUNW6T62', 'Amazon PLCC Free-Financing Universal Merchant AAT-G5ZRX4BZOIODU', 'Amazon PLCC Free-Financing Universal Merchant AAT-P3CSUAK4HTEP2', 'Amazon PLCC Free-Financi

In [142]:
df_cleaned = df_cleaned.with_columns(
    [
        pl.when(col("promotion-ids").is_not_null())
        .then(col("promotion-ids").str.count_matches(promotion_type))
        .otherwise(0)
        .alias(f"promotion_type{i+1}_count")
        for i, promotion_type in enumerate(promotion_types)
    ]
)
df_cleaned.head()

shape: (5, 23)
┌────────────┬──────────┬────────────┬────────────┬───┬────────────┬───────┬───────────┬───────────┐
│ Order-ID   ┆ Date     ┆ Status     ┆ Fulfilment ┆ … ┆ promotion- ┆ B2B   ┆ promotion ┆ promotion │
│ ---        ┆ ---      ┆ ---        ┆ ---        ┆   ┆ ids        ┆ ---   ┆ _type1_co ┆ _type2_co │
│ str        ┆ str      ┆ str        ┆ str        ┆   ┆ ---        ┆ bool  ┆ unt       ┆ unt       │
│            ┆          ┆            ┆            ┆   ┆ str        ┆       ┆ ---       ┆ ---       │
│            ┆          ┆            ┆            ┆   ┆            ┆       ┆ i64       ┆ i64       │
╞════════════╪══════════╪════════════╪════════════╪═══╪════════════╪═══════╪═══════════╪═══════════╡
│ 405-807878 ┆ 04-30-22 ┆ Cancelled  ┆ Merchant   ┆ … ┆ null       ┆ false ┆ 0         ┆ 0         │
│ 4-5731545  ┆          ┆            ┆            ┆   ┆            ┆       ┆           ┆           │
│ 171-919815 ┆ 04-30-22 ┆ Shipped -  ┆ Merchant   ┆ … ┆ Amazon     ┆ false ┆ 25        ┆ 0         │
│ 1-1101146  ┆          ┆ Delivered  ┆            ┆   ┆ PLCC Free- ┆       ┆           ┆           │
│            ┆          ┆ to Buyer   ┆            ┆   ┆ Financing  ┆       ┆           ┆           │
│            ┆          ┆            ┆            ┆   ┆ Uni…       ┆       ┆           ┆           │
│ 404-068767 ┆ 04-30-22 ┆ Shipped    ┆ Amazon     ┆ … ┆ IN Core    ┆ true  ┆ 0         ┆ 1         │
│ 6-7273146  ┆          ┆            ┆            ┆   ┆ Free       ┆       ┆           ┆           │
│            ┆          ┆            ┆            ┆   ┆ Shipping   ┆       ┆           ┆           │
│            ┆          ┆            ┆            ┆   ┆ 2015/04/…  ┆       ┆           ┆           │
│ 403-961537 ┆ 04-30-22 ┆ Cancelled  ┆ Merchant   ┆ … ┆ null       ┆ false ┆ 0         ┆ 0         │
│ 7-8133951  ┆          ┆            ┆            ┆   ┆            ┆       ┆           ┆           │
│ 407-106979 ┆ 04-30-22 ┆ Shipped    ┆ Amazon     ┆ … ┆ null       ┆ false ┆ 0         ┆ 0         │
│ 0-7240320  ┆          ┆            ┆            ┆   ┆            ┆       ┆           ┆           │
└────────────┴──────────┴────────────┴────────────┴───┴────────────┴───────┴───────────┴───────────┘

In [143]:
# We will not use promotion-ids column anymore
df_cleaned = df_cleaned.drop('promotion-ids')

In [144]:
df_cleaned.null_count()

shape: (1, 22)
┌──────────┬──────┬────────┬────────────┬───┬──────────────┬─────┬────────────────┬────────────────┐
│ Order-ID ┆ Date ┆ Status ┆ Fulfilment ┆ … ┆ ship-country ┆ B2B ┆ promotion_type ┆ promotion_type │
│ ---      ┆ ---  ┆ ---    ┆ ---        ┆   ┆ ---          ┆ --- ┆ 1_count        ┆ 2_count        │
│ u32      ┆ u32  ┆ u32    ┆ u32        ┆   ┆ u32          ┆ u32 ┆ ---            ┆ ---            │
│          ┆      ┆        ┆            ┆   ┆              ┆     ┆ u32            ┆ u32            │
╞══════════╪══════╪════════╪════════════╪═══╪══════════════╪═════╪════════════════╪════════════════╡
│ 0        ┆ 0    ┆ 0      ┆ 0          ┆ … ┆ 0            ┆ 0   ┆ 0              ┆ 0              │
└──────────┴──────┴────────┴────────────┴───┴──────────────┴─────┴────────────────┴────────────────┘

Missing values is Done.


## 2.2 Data Type Conversion


In [145]:
df_cleaned.glimpse(max_items_per_column=5)

Rows: 128940
Columns: 22
$ Order-ID               <str> '405-8078784-5731545', '171-9198151-1101146', '404-0687676-7273146', '403-9615377-8133951', '407-1069790-7240320'
$ Date                   <str> '04-30-22', '04-30-22', '04-30-22', '04-30-22', '04-30-22'
$ Status                 <str> 'Cancelled', 'Shipped - Delivered to Buyer', 'Shipped', 'Cancelled', 'Shipped'
$ Fulfilment             <str> 'Merchant', 'Merchant', 'Amazon', 'Merchant', 'Amazon'
$ Sales-Channel          <str> 'Amazon.in', 'Amazon.in', 'Amazon.in', 'Amazon.in', 'Amazon.in'
$ ship-service-level     <str> 'Standard', 'Standard', 'Expedited', 'Standard', 'Expedited'
$ Style                  <str> 'SET389', 'JNE3781', 'JNE3371', 'J0341', 'JNE3671'
$ SKU                    <str> 'SET389-KR-NP-S', 'JNE3781-KR-XXXL', 'JNE3371-KR-XL', 'J0341-DR-L', 'JNE3671-TU-XXXL'
$ Category               <str> 'Set', 'kurta', 'kurta', 'Western Dress', 'Top'
$ Size                   <str> 'S', '3XL', 'XL', 'L', '3XL'
$ ASIN             

In [146]:
df_raw.estimated_size('mb')

62.78241729736328

In [147]:
# Estimated_size In with big useless dtype
df_cleaned.estimated_size('mb')

21.07734489440918

In [148]:
df_cleaned = df_cleaned.with_columns([
    col("Date")                 .str.strptime(pl.Date, format="%m-%d-%y"),
    col("ship-city")            .str.to_titlecase(),
    col("ship-state")           .str.to_titlecase(),
    col("Qty")                  .cast(pl.UInt8),
    col("Amount")               .cast(pl.Float32),
    col("ship-postal-code")     .cast(pl.UInt32),
    col("promotion_type1_count").cast(pl.UInt8),
    col("promotion_type2_count").cast(pl.UInt8),
])
# because it have one unique value for all rows -> we can drop it
df_cleaned = df_cleaned.drop('ship-country')
df_cleaned.head()

shape: (5, 21)
┌────────────┬────────────┬────────────┬───────────┬───┬───────────┬───────┬───────────┬───────────┐
│ Order-ID   ┆ Date       ┆ Status     ┆ Fulfilmen ┆ … ┆ ship-post ┆ B2B   ┆ promotion ┆ promotion │
│ ---        ┆ ---        ┆ ---        ┆ t         ┆   ┆ al-code   ┆ ---   ┆ _type1_co ┆ _type2_co │
│ str        ┆ date       ┆ str        ┆ ---       ┆   ┆ ---       ┆ bool  ┆ unt       ┆ unt       │
│            ┆            ┆            ┆ str       ┆   ┆ u32       ┆       ┆ ---       ┆ ---       │
│            ┆            ┆            ┆           ┆   ┆           ┆       ┆ u8        ┆ u8        │
╞════════════╪════════════╪════════════╪═══════════╪═══╪═══════════╪═══════╪═══════════╪═══════════╡
│ 405-807878 ┆ 2022-04-30 ┆ Cancelled  ┆ Merchant  ┆ … ┆ 400081    ┆ false ┆ 0         ┆ 0         │
│ 4-5731545  ┆            ┆            ┆           ┆   ┆           ┆       ┆           ┆           │
│ 171-919815 ┆ 2022-04-30 ┆ Shipped -  ┆ Merchant  ┆ … ┆ 560085    ┆ false ┆ 25        ┆ 0         │
│ 1-1101146  ┆            ┆ Delivered  ┆           ┆   ┆           ┆       ┆           ┆           │
│            ┆            ┆ to Buyer   ┆           ┆   ┆           ┆       ┆           ┆           │
│ 404-068767 ┆ 2022-04-30 ┆ Shipped    ┆ Amazon    ┆ … ┆ 410210    ┆ true  ┆ 0         ┆ 1         │
│ 6-7273146  ┆            ┆            ┆           ┆   ┆           ┆       ┆           ┆           │
│ 403-961537 ┆ 2022-04-30 ┆ Cancelled  ┆ Merchant  ┆ … ┆ 605008    ┆ false ┆ 0         ┆ 0         │
│ 7-8133951  ┆            ┆            ┆           ┆   ┆           ┆       ┆           ┆           │
│ 407-106979 ┆ 2022-04-30 ┆ Shipped    ┆ Amazon    ┆ … ┆ 600073    ┆ false ┆ 0         ┆ 0         │
│ 0-7240320  ┆            ┆            ┆           ┆   ┆           ┆       ┆           ┆           │
└────────────┴────────────┴────────────┴───────────┴───┴───────────┴───────┴───────────┴───────────┘

In [149]:
df_cleaned['Sales-Channel'].value_counts()

shape: (2, 2)
┌───────────────┬────────┐
│ Sales-Channel ┆ count  │
│ ---           ┆ ---    │
│ str           ┆ u32    │
╞═══════════════╪════════╡
│ Non-Amazon    ┆ 124    │
│ Amazon.in     ┆ 128816 │
└───────────────┴────────┘

In [150]:
df_cleaned = df_cleaned.with_columns(
    (col("Sales-Channel") == "Amazon.in").name.suffix("_is_amazon")
)
df_cleaned = df_cleaned.drop('Sales-Channel')
df_cleaned.head()

shape: (5, 21)
┌────────────┬────────────┬────────────┬───────────┬───┬───────┬───────────┬───────────┬───────────┐
│ Order-ID   ┆ Date       ┆ Status     ┆ Fulfilmen ┆ … ┆ B2B   ┆ promotion ┆ promotion ┆ Sales-Cha │
│ ---        ┆ ---        ┆ ---        ┆ t         ┆   ┆ ---   ┆ _type1_co ┆ _type2_co ┆ nnel_is_a │
│ str        ┆ date       ┆ str        ┆ ---       ┆   ┆ bool  ┆ unt       ┆ unt       ┆ mazon     │
│            ┆            ┆            ┆ str       ┆   ┆       ┆ ---       ┆ ---       ┆ ---       │
│            ┆            ┆            ┆           ┆   ┆       ┆ u8        ┆ u8        ┆ bool      │
╞════════════╪════════════╪════════════╪═══════════╪═══╪═══════╪═══════════╪═══════════╪═══════════╡
│ 405-807878 ┆ 2022-04-30 ┆ Cancelled  ┆ Merchant  ┆ … ┆ false ┆ 0         ┆ 0         ┆ true      │
│ 4-5731545  ┆            ┆            ┆           ┆   ┆       ┆           ┆           ┆           │
│ 171-919815 ┆ 2022-04-30 ┆ Shipped -  ┆ Merchant  ┆ … ┆ false ┆ 25        ┆ 0         ┆ true      │
│ 1-1101146  ┆            ┆ Delivered  ┆           ┆   ┆       ┆           ┆           ┆           │
│            ┆            ┆ to Buyer   ┆           ┆   ┆       ┆           ┆           ┆           │
│ 404-068767 ┆ 2022-04-30 ┆ Shipped    ┆ Amazon    ┆ … ┆ true  ┆ 0         ┆ 1         ┆ true      │
│ 6-7273146  ┆            ┆            ┆           ┆   ┆       ┆           ┆           ┆           │
│ 403-961537 ┆ 2022-04-30 ┆ Cancelled  ┆ Merchant  ┆ … ┆ false ┆ 0         ┆ 0         ┆ true      │
│ 7-8133951  ┆            ┆            ┆           ┆   ┆       ┆           ┆           ┆           │
│ 407-106979 ┆ 2022-04-30 ┆ Shipped    ┆ Amazon    ┆ … ┆ false ┆ 0         ┆ 0         ┆ true      │
│ 0-7240320  ┆            ┆            ┆           ┆   ┆       ┆           ┆           ┆           │
└────────────┴────────────┴────────────┴───────────┴───┴───────┴───────────┴───────────┴───────────┘

In [151]:
# Get the estimated sizes in megabytes
old_size = df_raw.estimated_size('mb')
final_size = df_cleaned.estimated_size('mb')

# Calculate the improvement
size_reduction = old_size - final_size
percentage_reduction = (size_reduction / old_size) * \
    100 if old_size != 0 else 0

print(f"Old size            : {old_size:.2f} MB")
print(f"Final size          : {final_size:.2f} MB")
print(f"Size reduction      : {size_reduction:.2f} MB")
print(f"Percentage reduction: {percentage_reduction:.2f}%")

Old size            : 62.78 MB
Final size          : 15.61 MB
Size reduction      : 47.17 MB
Percentage reduction: 75.13%


## 2.3 Outlier Detection and Treatment


In [152]:
print("All Numeric Columns:")
for col_ in df_cleaned:
    if col_.dtype.is_numeric():
        print(
            f"name: {col_.name:<21}, min: {col_.min():>7_}, max: {col_.max():_}")

All Numeric Columns:
name: Qty                  , min:       0, max: 15
name: Amount               , min:     0.0, max: 5_584.0
name: ship-postal-code     , min: 110_001, max: 989_898
name: promotion_type1_count, min:       0, max: 36
name: promotion_type2_count, min:       0, max: 1


In [153]:
def lower_and_upper_bound(col_) -> tuple[float, float]:
    q1 = float(col_.quantile(0.25) or 0)
    q3 = float(col_.quantile(0.75) or 0)
    iqr = q3 - q1
    upper_bound = q3 + 1.5 * iqr
    lower_bound = q1 - 1.5 * iqr
    return lower_bound, upper_bound

In [154]:
df_cleaned['Qty'].value_counts()

shape: (10, 2)
┌─────┬────────┐
│ Qty ┆ count  │
│ --- ┆ ---    │
│ u8  ┆ u32    │
╞═════╪════════╡
│ 0   ┆ 12802  │
│ 2   ┆ 341    │
│ 4   ┆ 9      │
│ 5   ┆ 2      │
│ 13  ┆ 1      │
│ 9   ┆ 1      │
│ 15  ┆ 1      │
│ 8   ┆ 1      │
│ 3   ┆ 32     │
│ 1   ┆ 115750 │
└─────┴────────┘

In [155]:
df_cleaned.select(['Qty', 'Date']).plot.line(
    x='Date', y='Qty', title='The `Qty` over time')

:Curve   [Date]   (Qty)

In [156]:
print(lower_and_upper_bound(df_cleaned['Qty']))
# here we this not outliers because we want to see all Quantity levels [not so many levels]

(1.0, 1.0)


In [157]:
df_cleaned.select(['Amount', 'Date']).plot.line(
    x='Date', y='Amount', title='The `Amount` over time')

:Curve   [Date]   (Amount)

you can see that there are outliers in `Amount` not all in the same behaver


In [158]:
df_cleaned['Amount'].plot.box(title='The Distribution of Dirty `Amount`')

:BoxWhisker   (Amount)

In [159]:
amount_lower_bound, amount_upper_bound = lower_and_upper_bound(
    df_cleaned['Amount'])
amount_lower_bound, amount_upper_bound

(-124.0, 1308.0)

In [160]:
df_cleaned = df_cleaned.filter(
    df_cleaned['Amount'].is_between(
        amount_lower_bound, amount_upper_bound)
)

In [161]:
df_cleaned['Amount'].plot.box(title='The Distribution of Clean `Amount`')

:BoxWhisker   (Amount)

In [162]:
df_cleaned.select(['Amount', 'Date']).plot.line(
    x='Date', y='Amount', title='The `Amount` over time')

:Curve   [Date]   (Amount)

you can see that there are no outliers in `Amount` and all in the same behaver


### Outliers Conclusion:

1. `Qty` column here we this not outliers because we want to see all Quantity levels [not so many levels].
2. `Amount` column have outliers and we removed them.
3. `ship-postal-code` column we considered as categorical column.
4. `promotion_type1_count` we want to learn all level of this column because it's values have many data in distributed levels.


In [163]:
df_cleaned.estimated_size('mb')

15.233895301818848

In [164]:
df_cleaned.write_csv("Amazon_Sale_Report_Cleaned.csv")

# 3: Data Visualization


In [2]:
import plotly.express as px
import polars as pl
from polars import col

In [3]:
df = pl.read_csv("Amazon_Sale_Report_Cleaned.csv")
df.head(2), df.estimated_size('mb')

(shape: (2, 21)
 ┌────────────┬────────────┬────────────┬───────────┬───┬───────┬───────────┬───────────┬───────────┐
 │ Order-ID   ┆ Date       ┆ Status     ┆ Fulfilmen ┆ … ┆ B2B   ┆ promotion ┆ promotion ┆ Sales-Cha │
 │ ---        ┆ ---        ┆ ---        ┆ t         ┆   ┆ ---   ┆ _type1_co ┆ _type2_co ┆ nnel_is_a │
 │ str        ┆ str        ┆ str        ┆ ---       ┆   ┆ bool  ┆ unt       ┆ unt       ┆ mazon     │
 │            ┆            ┆            ┆ str       ┆   ┆       ┆ ---       ┆ ---       ┆ ---       │
 │            ┆            ┆            ┆           ┆   ┆       ┆ i64       ┆ i64       ┆ bool      │
 ╞════════════╪════════════╪════════════╪═══════════╪═══╪═══════╪═══════════╪═══════════╪═══════════╡
 │ 405-807878 ┆ 2022-04-30 ┆ Cancelled  ┆ Merchant  ┆ … ┆ false ┆ 0         ┆ 0         ┆ true      │
 │ 4-5731545  ┆            ┆            ┆           ┆   ┆       ┆           ┆           ┆           │
 │ 171-919815 ┆ 2022-04-30 ┆ Shipped -  ┆ Merchant  ┆ … ┆ false ┆ 

In [4]:
df = df.with_columns([
    col("Date")                 .str.strptime(pl.Date, format="%Y-%m-%d"),
    col("Qty")                  .cast(pl.UInt8),
    col("Amount")               .cast(pl.Float32),
    col("ship-postal-code")     .cast(pl.UInt32),
    col("promotion_type1_count").cast(pl.UInt8),
    col("promotion_type2_count").cast(pl.UInt8),
])
df.head(2), df.estimated_size('mb')

(shape: (2, 21)
 ┌────────────┬────────────┬────────────┬───────────┬───┬───────┬───────────┬───────────┬───────────┐
 │ Order-ID   ┆ Date       ┆ Status     ┆ Fulfilmen ┆ … ┆ B2B   ┆ promotion ┆ promotion ┆ Sales-Cha │
 │ ---        ┆ ---        ┆ ---        ┆ t         ┆   ┆ ---   ┆ _type1_co ┆ _type2_co ┆ nnel_is_a │
 │ str        ┆ date       ┆ str        ┆ ---       ┆   ┆ bool  ┆ unt       ┆ unt       ┆ mazon     │
 │            ┆            ┆            ┆ str       ┆   ┆       ┆ ---       ┆ ---       ┆ ---       │
 │            ┆            ┆            ┆           ┆   ┆       ┆ u8        ┆ u8        ┆ bool      │
 ╞════════════╪════════════╪════════════╪═══════════╪═══╪═══════╪═══════════╪═══════════╪═══════════╡
 │ 405-807878 ┆ 2022-04-30 ┆ Cancelled  ┆ Merchant  ┆ … ┆ false ┆ 0         ┆ 0         ┆ true      │
 │ 4-5731545  ┆            ┆            ┆           ┆   ┆       ┆           ┆           ┆           │
 │ 171-919815 ┆ 2022-04-30 ┆ Shipped -  ┆ Merchant  ┆ … ┆ false ┆ 

In [5]:
df.glimpse()

Rows: 125771
Columns: 21
$ Order-ID                 <str> '405-8078784-5731545', '171-9198151-1101146', '404-0687676-7273146', '403-9615377-8133951', '407-1069790-7240320', '404-1490984-4578765', '408-5748499-6859555', '406-7807733-3785945', '407-5443024-5233168', '402-4393761-0311520'
$ Date                    <date> 2022-04-30, 2022-04-30, 2022-04-30, 2022-04-30, 2022-04-30, 2022-04-30, 2022-04-30, 2022-04-30, 2022-04-30, 2022-04-30
$ Status                   <str> 'Cancelled', 'Shipped - Delivered to Buyer', 'Shipped', 'Cancelled', 'Shipped', 'Shipped', 'Shipped', 'Shipped - Delivered to Buyer', 'Cancelled', 'Shipped'
$ Fulfilment               <str> 'Merchant', 'Merchant', 'Amazon', 'Merchant', 'Amazon', 'Amazon', 'Amazon', 'Merchant', 'Amazon', 'Amazon'
$ ship-service-level       <str> 'Standard', 'Standard', 'Expedited', 'Standard', 'Expedited', 'Expedited', 'Expedited', 'Standard', 'Expedited', 'Expedited'
$ Style                    <str> 'SET389', 'JNE3781', 'JNE3371', 'J0341',

### 3.1 What is the overall sales distribution by status?


In [5]:
status_dist = df['Status'].value_counts().sort(
    by='count').top_k(5, by='count')
px.pie(
    status_dist.to_pandas(),
    names='Status',
    values='count',
    title='The percentage of 5 Top Most `Status` Type Big')

The Most two big `Status` type is `Shipped` and `Delivered to Buyer`. <br>
this means Success


### 3.2 What is the monthly trend of total sales and the number of orders?


In [31]:
t_df = df.group_by([col("Date").dt.month().alias("Month")]).agg(
    col("Order-ID").count().alias("Order Count")
).sort(by='Order Count', descending=True)\
    .to_pandas()

px.bar(t_df,
       x='Month',
       y='Order Count',
       template='seaborn',
       title='The Order Count by Month', orientation='v')

we can infer that the peak month is `April` in sales.


### 3.3. What are the top-performing categories in terms of Amount volume?


In [34]:
tdf = df.group_by('Category').agg(
    (col('Amount').sum()/10e6).alias('Mean Amount')
).sort(by='Mean Amount', descending=True).to_pandas()

px.bar(tdf,
       x='Category',
       y='Mean Amount',
       template='seaborn',
       title='Mean Amount by Category', orientation='v')

we can infer that the most popular category is `Women's Clothing`. <br>
so, we need to focus on this category and add any category to them.


### 3.4 How does the shipping service level affect the order status?


In [49]:
t_df = df.group_by(['Status', 'ship-service-level']).agg(
    col('Order-ID').count().alias('count')
).to_pandas()

fig = px.density_heatmap(
    t_df,
    x='ship-service-level',
    y='Status',
    z='count',
    color_continuous_scale='Viridis',
    title='Relationship between `Order Status` and `Shipping Service Level`',
    width=800
)

fig.show()

see that,

- when teh `shipping service level` is Expedited so the `Order Status` is Shipped that means good service.
- the orders that `shipping service level` is **Expedited** most likely to make the `order Status` canceled **More** the the **Standard** level
- and if the `shipping service level` is **Standard** it make more stable `order status` **Shipped - Delivered to Buyer**


### 3.5 What is the geographical distribution of orders?


In [19]:
import plotly.express as px
from opencage.geocoder import OpenCageGeocode
import polars as pl
import time

# Replace 'YOUR_API_KEY' with your actual OpenCage API key
key = 'd6cb0afb356549be9e09eef22b446f0f'
geocoder = OpenCageGeocode(key)


def geocode(city, state):
    query = f"{city}, {state}, India"
    result = geocoder.geocode(query, no_annotations='1')
    if result and len(result):
        # type: ignore
        # type: ignore
        return result[0]['geometry']['lat'], result[0]['geometry']['lng']
    return None, None


# Aggregating data by city and state
temp_location_df = df.group_by(['ship-city', 'ship-state']).agg(
    pl.col('Order-ID').count().alias('Order Count')
)

temp_location_df = temp_location_df.sort(by='Order Count', descending=True).filter(
    col("Order Count") > 50
).to_pandas()

# Geocoding
coordinates = []
for index, row in temp_location_df.iterrows():
    lat, lon = geocode(row['ship-city'], row['ship-state'])
    coordinates.append((lat, lon))
    time.sleep(1)  # Adding delay to avoid hitting rate limits

temp_location_df['Latitude'], temp_location_df['Longitude'] = zip(*coordinates)
temp_location_df = temp_location_df.dropna(subset=['Latitude', 'Longitude'])
temp_location_df[['ship-city', 'Latitude', 'Longitude']
                 ].to_csv('ship-city-location.csv', index=False)

In [20]:
temp_location_df = pd.read_csv('ship-city-location.csv')
temp_location_df = temp_location_df.set_index('ship-city')


def gen_map_df_based_count(col_name):

    tdf = df.group_by(['ship-city', 'ship-state']).agg(
        col(col_name).count().name.suffix('_count')
    ).top_k(20, by=f'{col_name}_count').to_pandas()

    tdf[['latitude', 'longitude']] = tdf.apply(
        lambda row: temp_location_df.loc[row['ship-city']], axis=1, result_type='expand')

    return tdf


def gen_map_df_based_sum(col_name):

    tdf = df.group_by(['ship-city', 'ship-state']).agg(
        col(col_name).sum().name.suffix('_sum')
    ).top_k(20, by=f'{col_name}_sum').to_pandas()

    tdf[['latitude', 'longitude']] = tdf.apply(
        lambda row: temp_location_df.loc[row['ship-city']], axis=1, result_type='expand')

    return tdf


def gen_map_chart(tdf, col_name, title_col_name):

    # Create the scatter plot on the map
    fig = px.scatter_geo(
        tdf,
        lat='latitude',
        lon='longitude',
        size=col_name,
        color='ship-city',
        hover_name='ship-city',
        hover_data={'ship-state': True, col_name: True,
                    'latitude': False, 'longitude': False},
        title=f'Geographical Distribution of {title_col_name} by City',
        projection='natural earth',
        width=700
    )
    fig.update_layout(
        geo=dict(
            scope='asia',  # Focus on the Asia region, including India
            coastlinecolor="gray",
            projection_scale=3,  # Adjust for zoom level
            center={"lat": 20.5937, "lon": 78.9629}  # Center of India
        )
    )
    return fig


tdf = gen_map_df_based_count('Order-ID')
gen_map_chart(tdf, 'Order-ID_count', 'Orders Numbers')

c:\Users\hima\AppData\Local\Programs\Python\Python311\Lib\site-packages\plotly\express\_core.py:1980: FutureWarning: When grouping with a length-1 list-like, you will need to pass a length-1 tuple to get_group in a future version of pandas. Pass `(name,)` instead of `name` to silence this warning.
  sf: grouped.get_group(s if len(s) > 1 else s[0])


the most popular city is `bengaluru` and `hyderabad` in ordering orders.


### 3.6 What are the trends in B2B vs. B2C sales?


In [185]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots


def gen_b2b_b2c_scatter_plot(df) -> go.Figure:

    t_df = df.with_columns(
        col("B2B").replace({False: "B2C", True: "B2B"})
    ).select(['Date', 'B2B']).group_by(["Date", 'B2B']).len()

    # Create subplot layout
    fig = make_subplots(
        rows=1, cols=2,  # 1 row and 2 columns
        subplot_titles=("B2B Data", "B2C Data")
    )

    b2b_data = t_df.filter(col('B2B') == 'B2B')
    b2c_data = t_df.filter(col('B2B') == 'B2C')

    fig.add_trace(
        go.Scatter(x=b2b_data['Date'], y=b2b_data['len'],
                   mode='markers', name='B2B'),
        row=1, col=1
    )

    fig.add_trace(
        go.Scatter(x=b2c_data['Date'], y=b2c_data['len'],
                   mode='markers', name='B2C'),
        row=1, col=2
    )

    # Update layout
    fig.update_layout(
        title_text="B2B vs. B2C",
        showlegend=False  # Show or hide legend based on preference
    )

    # Show plot
    return fig

In [186]:
gen_b2b_b2c_scatter_plot(df).show()

as you can see,

- Number of orders of `B2B` orders are not in recognizable patterns.
- And `B2C` orders are in recognizable patterns.
- The Numbers of `B2C` orders are higher than `B2B` orders.


### 3.7 Fulfilment Method Distribution


In [208]:
tdf = df.group_by(['Date', 'Fulfilment']).agg(
    col('Order-ID').count().alias('order_count')).to_pandas()

px.scatter(tdf, x='Date', y='order_count', color='Fulfilment',
           title='Fulfilment Over Time', width=700)

we can infer that when the number of Amazon fulfillment decrease, the number of Merchant fulfillment orders increase. <br>
the Amazon and Merchant fulfillment in negative relationship.


In [21]:
df.group_by([col("Date").dt.month().alias("Date")]).agg(
    col('Amount').mean().alias('mean_amount')
)

shape: (4, 2)
┌──────┬─────────────┐
│ Date ┆ mean_amount │
│ ---  ┆ ---         │
│ i8   ┆ f32         │
╞══════╪═════════════╡
│ 3    ┆ 582.182495  │
│ 6    ┆ 598.408081  │
│ 4    ┆ 573.907532  │
│ 5    ┆ 595.732666  │
└──────┴─────────────┘

In [36]:
df['Amount'].sum()

73963936.0

In [35]:
df['Qty'].sum()

113294

In [5]:
df.group_by([col("Date")]).agg(
    col('Qty').mean().alias('mean_amount')
).plot.line(x='Date', y='mean_amount', title='The Mean Amount Over Time')

:Curve   [Date]   (mean_amount)

# 4: Predictive Modeling


In [203]:
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report, accuracy_score
import polars as pl
from polars import col


import warnings
warnings.filterwarnings('ignore')

In [2]:
df = pl.read_csv('Amazon_Sale_Report_Cleaned.csv')
df = df.with_columns([
    col("Date")                 .str.strptime(pl.Date, format="%Y-%m-%d"),
    col("Qty")                  .cast(pl.UInt8),
    col("Amount")               .cast(pl.Float32),
    col("ship-postal-code")     .cast(pl.UInt32),
    col("promotion_type1_count").cast(pl.UInt8),
    col("promotion_type2_count").cast(pl.UInt8),
])
df.head(2)

shape: (2, 21)
┌────────────┬────────────┬────────────┬───────────┬───┬───────┬───────────┬───────────┬───────────┐
│ Order-ID   ┆ Date       ┆ Status     ┆ Fulfilmen ┆ … ┆ B2B   ┆ promotion ┆ promotion ┆ Sales-Cha │
│ ---        ┆ ---        ┆ ---        ┆ t         ┆   ┆ ---   ┆ _type1_co ┆ _type2_co ┆ nnel_is_a │
│ str        ┆ date       ┆ str        ┆ ---       ┆   ┆ bool  ┆ unt       ┆ unt       ┆ mazon     │
│            ┆            ┆            ┆ str       ┆   ┆       ┆ ---       ┆ ---       ┆ ---       │
│            ┆            ┆            ┆           ┆   ┆       ┆ u8        ┆ u8        ┆ bool      │
╞════════════╪════════════╪════════════╪═══════════╪═══╪═══════╪═══════════╪═══════════╪═══════════╡
│ 405-807878 ┆ 2022-04-30 ┆ Cancelled  ┆ Merchant  ┆ … ┆ false ┆ 0         ┆ 0         ┆ true      │
│ 4-5731545  ┆            ┆            ┆           ┆   ┆       ┆           ┆           ┆           │
│ 171-919815 ┆ 2022-04-30 ┆ Shipped -  ┆ Merchant  ┆ … ┆ false ┆ 25        ┆ 0         ┆ true      │
│ 1-1101146  ┆            ┆ Delivered  ┆           ┆   ┆       ┆           ┆           ┆           │
│            ┆            ┆ to Buyer   ┆           ┆   ┆       ┆           ┆           ┆           │
└────────────┴────────────┴────────────┴───────────┴───┴───────┴───────────┴───────────┴───────────┘

In [3]:
df.glimpse(max_items_per_column=5)

Rows: 125771
Columns: 21
$ Order-ID                 <str> '405-8078784-5731545', '171-9198151-1101146', '404-0687676-7273146', '403-9615377-8133951', '407-1069790-7240320'
$ Date                    <date> 2022-04-30, 2022-04-30, 2022-04-30, 2022-04-30, 2022-04-30
$ Status                   <str> 'Cancelled', 'Shipped - Delivered to Buyer', 'Shipped', 'Cancelled', 'Shipped'
$ Fulfilment               <str> 'Merchant', 'Merchant', 'Amazon', 'Merchant', 'Amazon'
$ ship-service-level       <str> 'Standard', 'Standard', 'Expedited', 'Standard', 'Expedited'
$ Style                    <str> 'SET389', 'JNE3781', 'JNE3371', 'J0341', 'JNE3671'
$ SKU                      <str> 'SET389-KR-NP-S', 'JNE3781-KR-XXXL', 'JNE3371-KR-XL', 'J0341-DR-L', 'JNE3671-TU-XXXL'
$ Category                 <str> 'Set', 'kurta', 'kurta', 'Western Dress', 'Top'
$ Size                     <str> 'S', '3XL', 'XL', 'L', '3XL'
$ ASIN                     <str> 'B09KXVBD7Z', 'B09K3WFS32', 'B07WV4JV4D', 'B099NRCT7B', 'B09871

In [4]:
df = df.with_columns(
    day=col('Date').dt.day().cast(pl.UInt8),
    month=col('Date').dt.month().cast(pl.UInt8),
)

In [5]:
features = ['Fulfilment',
            'ship-service-level',
            'Style',
            'Size',
            'Qty',
            'Amount',
            'B2B',
            'Category',
            'Courier-Status',
            'ship-city',
            'ship-state',
            'promotion_type1_count',
            'promotion_type2_count',
            'Sales-Channel_is_amazon',
            'month',
            'day'
            ]

In [6]:
df = df.with_columns(
    col("Sales-Channel_is_amazon").map_dict({True: 1, False: 0}).cast(pl.UInt8)
)

In [7]:
pdf = df.select(features).to_pandas()

In [8]:
le = LabelEncoder()

for col_, col_type in zip(pdf.columns, pdf.dtypes):

    if col_type == 'object':

        pdf[col_] = le.fit_transform(pdf[col_])

In [9]:
y = le.fit_transform(df['Status'])
X = pdf
X.head(), y

(   Fulfilment  ship-service-level  Style  Size  Qty      Amount    B2B  \
 0           1                   1   1340     7    0  647.619995  False   
 1           1                   1    845     0    1  406.000000  False   
 2           0                   0    531     8    1  329.000000   True   
 3           1                   1    371     5    0  753.330017  False   
 4           0                   0    752     0    1  574.000000  False   
 
    Category  Courier-Status  ship-city  ship-state  promotion_type1_count  \
 0         5               0       4282          22                      0   
 1         8               1        801          17                     25   
 2         8               1       4613          22                      0   
 3         7               0       5392          33                      0   
 4         6               1       1299          41                      0   
 
    promotion_type2_count  Sales-Channel_is_amazon  month  day  
 0           

In [10]:
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, random_state=42)

In [50]:
# Initialize the model
model_lr = LogisticRegression()

# Train the model
model_lr.fit(X_train, y_train)

# Predictions
y_pred_lr = model_lr.predict(X_test)

# Evaluate the model
print("Logistic Regression Accuracy:", accuracy_score(y_test, y_pred_lr))
print("Classification Report:")
print(classification_report(y_test, y_pred_lr))

Logistic Regression Accuracy: 0.8436891274100576
Classification Report:
              precision    recall  f1-score   support

           0       0.74      0.39      0.51      3637
           1       0.00      0.00      0.00       122
           2       0.00      0.00      0.00        63
           3       0.84      0.98      0.90     15114
           5       0.89      0.89      0.89      5620
           6       0.00      0.00      0.00         1
           7       0.00      0.00      0.00         3
           8       0.00      0.00      0.00       190
           9       0.00      0.00      0.00         2
          10       0.00      0.00      0.00       385
          11       0.00      0.00      0.00        18

    accuracy                           0.84     25155
   macro avg       0.22      0.21      0.21     25155
weighted avg       0.81      0.84      0.82     25155



In [51]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import cross_val_score, StratifiedKFold

# Assuming you have prepared X and y data

# Initialize the model
model_rf = RandomForestClassifier()

# Perform 5-fold cross-validation
cv = StratifiedKFold(n_splits=5, shuffle=True)

# Perform cross-validation and obtain scores
cv_scores = cross_val_score(model_rf, X, y, cv=cv, scoring='accuracy')

# Train and predict on the whole dataset for final evaluation
model_rf.fit(X_train, y_train)
y_pred_rf = model_rf.predict(X_test)

In [52]:
# Print cross-validation scores
print("Cross-Validation Scores:", cv_scores)
print("Mean Accuracy:", cv_scores.mean())

# Evaluate the model on the whole dataset
print("\nFinal Evaluation on Whole Dataset:")
print("Random Forest Accuracy:", accuracy_score(y_test, y_pred_rf))
print("Classification Report:")
print(classification_report(y_test, y_pred_rf))

Cross-Validation Scores: [0.98052077 0.98024171 0.9809573  0.98067902 0.98040073]
Mean Accuracy: 0.9805599068078935

Final Evaluation on Whole Dataset:
Random Forest Accuracy: 0.98048101769032
Classification Report:
              precision    recall  f1-score   support

           0       0.99      1.00      1.00      3637
           1       0.96      0.89      0.92       122
           2       0.92      0.97      0.95        63
           3       1.00      1.00      1.00     15114
           5       0.93      1.00      0.96      5620
           6       0.00      0.00      0.00         1
           7       0.00      0.00      0.00         3
           8       0.91      0.86      0.88       190
           9       0.00      0.00      0.00         2
          10       0.50      0.01      0.02       385
          11       0.50      0.06      0.10        18

    accuracy                           0.98     25155
   macro avg       0.61      0.52      0.53     25155
weighted avg       0.97   

# So i will choose Random Forest Classifier.
